In [59]:
from sklearn.linear_model import SGDClassifier
import numpy as np
import collections
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import make_pipeline
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix
from scipy.special import logsumexp
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import datasets, transforms
from torch.utils.data import DataLoader
from torch.utils.data.sampler import SubsetRandomSampler
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset
from torch import Tensor
import geometry
import itertools
from collections import defaultdict
import collections
import target
import controler
import utils
from functools import reduce
import linear_regression
from multiprocessing import Pool
from functools import partial
import numpy as np
import geometry
import itertools 
from itertools import islice
import games
import feedexp3
import geometry_v2
import cpb
import feedexp3_v2
import bpm
import random_algo
import feedexp3_v3
import plotly.graph_objects as go

def evaluate_parallel(nbCores, n_folds, horizon, alg, game):
    print("nbCores:", nbCores, "nbFolds:", n_folds, "Horizon:", horizon)
    pool = Pool(processes = nbCores) 
    task = Evaluation(horizon)
    return np.asarray(  pool.map( partial( task.eval_policy_once, alg, game ), range(n_folds) ) ) 

def runif_in_simplex(n):
  ''' Return uniformly random vector in the n-simplex '''
  k = np.random.exponential(scale=1.0, size=n)
  return k / sum(k)

class Evaluation:

    def __init__(self, horizon ):
        self.horizon = horizon
        # self.outcome_distribution = outcome_distribution
    
    def get_outcomes(self, game, job_id):
        np.random.seed(job_id)
        # self.means = runif_in_simplex( self.game.n_outcomes )
        outcomes = np.random.choice( game.n_outcomes , p= list( game.outcome_dist.values() ), size= self.horizon) 
        return outcomes

    def get_feedback(self, game, action, outcome):
        return game.FeedbackMatrix[ action ][ outcome ]

    def eval_policy_once(self, alg, game, jobid):

        action_counter = np.zeros( (game.n_actions, self.horizon) )

        # generate outcomes obliviously
        outcomes = self.get_outcomes(game, jobid)

        for t in range(self.horizon):

            # policy chooses one action
            action = alg.get_action(t)

            # Environment chooses one outcome
            outcome = outcomes[t]
            feedback =  self.get_feedback( game, action, outcome )


            alg.update(action, feedback, outcome)
            print('t', t, 'action', action, 'outcome', outcome, )
            # print('nu', alg.nu / alg.n )

            for i in range(game.n_actions):
                if i == action:
                    action_counter[i][t] = action_counter[i][t-1] +1
                else:
                    action_counter[i][t] = action_counter[i][t-1]

        return action_counter

def eval_cpbvanilla_parallel(task, nbCores, n_folds, horizon, alpha):
    print("nbCores:", nbCores, "nbFolds:", n_folds, "Horizon:", horizon)
    pool = Pool(processes = nbCores) 
    return np.asarray(  pool.map( partial( task.cpb_vanilla_v2 ,alpha ), range(n_folds) ) ) 

def runif_in_simplex(n):
  ''' Return uniformly random vector in the n-simplex '''
  k = np.random.exponential(scale=1.0, size=n)
  return k / sum(k)


In [175]:

import geometry_v3
import numpy as np
import scipy

class TSPM_alg:

    def __init__(self, game, horizon,  ):
      self.game = game
      self.horizon = horizon

      self.N = game.n_actions
      self.M = game.n_outcomes
      self.A = geometry_v3.alphabet_size(game.FeedbackMatrix, self.N, self.M)
      print('n-actions', self.N, 'n-outcomes', self.M, 'alphabet', self.A)

      self.SignalMatrices = geometry_v3.calculate_signal_matrices(game.FeedbackMatrix, self.N, self.M, self.A)
      self.sts = [  s.T @ s  for s in  self.SignalMatrices ] 

      self.lbd = 0.001
      self.B0 = self.lbd * np.identity(self.M)
      self.b0 = np.zeros( (self.M, 1) ) 
      self.B = self.B0
      self.b = self.b0

      self.R = 1
      self.n = [ np.zeros( self.M ) for i in range(self.N) ]
      self.q = [ np.zeros( self.M ) for i in range(self.N) ]


    def in_simplex(self,p):
        res = False
        if p.sum() <= 1 and (p>=0).all():
            res = True
        return res

    def sample_from_g(self,):
        condition = False

        # 1. calc tilde{B} and tilde{b}
        one_vec = np.atleast_2d( np.ones(self.M - 1) ).T # \mathbb{1}_{M-1}
        # sub matrix of B
        C = self.B[:self.M-1, :self.M-1]
        d = np.atleast_2d( self.B[:self.M-1, -1] ).T
        D = (np.dot(d, one_vec.T) + np.dot(one_vec, d.T)) / 2
        f = self.B[-1, -1]
        # print('C', C, 'd', d, 'D', D, 'f', f)
        # sub vector of b
        b_alpha = np.atleast_2d( self.b[:self.M-1,0 ] ).T #0
        b_M = self.b[-1, 0] 
        B_tilde = C - 2 * D + f * np.dot(one_vec, one_vec.T)
        b_tilde = f * one_vec - d + b_alpha - b_M * one_vec

        B_tilde_inv = np.linalg.inv(B_tilde)
        Bb = B_tilde_inv @ b_tilde
        print( 'sampler dans la distribution:',  Bb, B_tilde_inv )

        while condition == False:
            p = np.random.normal( Bb, B_tilde_inv  )[0][0]
            print('echantillon',p)
            if p<=1 and p>=0: #self.in_simplex(p):
                condition = True
        print(p)
        return np.array( [ p , 1 - p ] )

    def accept_reject(self,):
        while True:
            p_tilde = self.sample_from_g()
            u_tilde = np.random.uniform(0, 1, self.M)
            print('F', self.F(p_tilde), 'G', self.G(p_tilde), 'F/G', self.F(p_tilde) / self.G(p_tilde) )
            print( 'mean', np.linalg.inv( self.B ) @ self.b , 'var', np.linalg.inv( self.B ) )
            if ( self.R * u_tilde < self.F(p_tilde) / self.G(p_tilde) ).all() :
                return p_tilde

    def F(self, p):
        result = 1
        for i in range(self.N):
            result *= np.exp( -self.n[i].sum() * scipy.special.kl_div( self.q[i], self.SignalMatrices[i] @ p )  )
        result *= p #norm.pdf(p ) loc = np.zeros(2) , scale = self.lbd * np.identity(self.M)
        return result

    def G(self,p):
        result = 1
        for i in range(self.N):
            result *= np.exp( -1/2 * self.n[i].sum() * np.linalg.norm( self.q[i] - self.SignalMatrices[i] @ p )**2  )
        result *= p #norm.pdf(p ) loc = np.zeros(2) , scale = self.lbd * np.identity(self.M)
        return result

    def get_action(self, t):

        if t < self.N * 10 * self.A :

            if t < 10 * self.A:
                action = 0
            elif t >= 10 * self.A and t < 20 * self.A:
                action = 1
            else:
                action: 2
                
        else:
            print('hello')
            p_tilde = self.accept_reject()
            action = np.argmax( [ self.game.LossMatrix[i,...] @ p_tilde for i in range(self.N)] )

        return action

    def update(self, action, feedback, outcome):

      self.B = self.B + self.sts[action]
      self.b = self.b + self.SignalMatrices[action].T @ np.eye(self.M)[outcome]
      
      self.n[action][outcome] += 1
      self.q[action] = [ self.n[action][i]/sum(self.n[action]) for i in range(self.N) ]
    #   print('B', self.B,'b',self.b , 'n', self.n,'q',self.q)

In [176]:
import TSPM

n_cores = 1
n_folds = 1
horizon = 100

outcome_distribution =  {'spam':0.05,'ham':0.95}

game = games.apple_tasting(False, outcome_distribution)
print('optimal action', game.i_star)
alg = TSPM_alg(  game, horizon,)
task = Evaluation(horizon)
a = task.eval_policy_once(alg,game,1)

optimal action 0
n-actions 2 n-outcomes 2 alphabet 2
t 0 action 0 outcome 1
t 1 action 0 outcome 1
t 2 action 0 outcome 0
t 3 action 0 outcome 1
t 4 action 0 outcome 1
t 5 action 0 outcome 1
t 6 action 0 outcome 1
t 7 action 0 outcome 1
t 8 action 0 outcome 1
t 9 action 0 outcome 1
t 10 action 0 outcome 1
t 11 action 0 outcome 1
t 12 action 0 outcome 1
t 13 action 0 outcome 1
t 14 action 0 outcome 0
t 15 action 0 outcome 1
t 16 action 0 outcome 1
t 17 action 0 outcome 1
t 18 action 0 outcome 1
t 19 action 0 outcome 1
t 20 action 1 outcome 1
t 21 action 1 outcome 1
t 22 action 1 outcome 1
t 23 action 1 outcome 1
t 24 action 1 outcome 1
t 25 action 1 outcome 1
t 26 action 1 outcome 1
t 27 action 1 outcome 0
t 28 action 1 outcome 1
t 29 action 1 outcome 1
t 30 action 1 outcome 1
t 31 action 1 outcome 1
t 32 action 1 outcome 1
t 33 action 1 outcome 1
t 34 action 1 outcome 1
t 35 action 1 outcome 1
t 36 action 1 outcome 1
t 37 action 1 outcome 1
t 38 action 1 outcome 0
t 39 action 1 outcome

KeyboardInterrupt: 

In [170]:
a = np.array( [[0.50118607]] )
a<=1

array([[ True]])

In [7]:
n_cores = 16
n_folds = 25
horizon = 2000

outcome_distribution =  {'spam':0.05,'ham':0.95}

game = games.apple_tasting(False, outcome_distribution)

algos = [ random_algo.Random(  game, horizon, ), 
           feedexp3.FeedExp3(  game, horizon, ),
           feedexp3_v3.FeedExp3(  game, horizon, ),
           cpb.CPB(  game, horizon,)  ] #bpm.BPM(  game, horizon,  [0.5, 0.5 ], np.identity(2) )

colors = [ [0,0,0], [255,128,0], [0,153,0], [204,0,102] ] #'cyan'
labels = ['random', 'FeedExp3 (2001)', 'FeedExp3 (2006)', 'CPB'] #'BPN


fig = go.Figure( )

for alg, color, label in zip( algos, colors, labels):

    r,g,b = color
    result = evaluate_parallel(n_cores, n_folds, horizon, alg, game)
    regret = np.array([ game.delta(i) for i in range(game.n_actions) ]).T @ np.mean(result,0) 
    xcoords = np.arange(0,horizon,1).tolist()
    std = np.array([ game.delta(i) for i in range(game.n_actions) ]).T @ np.std(result,0) 
    upper_regret = regret + std

    fig.add_trace(go.Scatter(x=xcoords, y=regret, line=dict(color='rgb({},{},{})'.format(r,g,b)), mode='lines',  name=label )) # 

    fig.add_trace(   go.Scatter( x=xcoords+xcoords[::-1], y=upper_regret.tolist()+regret.tolist()[::-1],  fill='toself', fillcolor='rgba({},{},{},0.2)'.format(r,g,b), 
                         line=dict(color='rgba(255,255,255,0)'),   hoverinfo="skip",  showlegend=False )

    )
    
fig.show(legend=True)
# fig.update_yaxes(range=[0, 30] )
# fig.show()


nbCores: 16 nbFolds: 25 Horizon: 2000
nbCores: 16 nbFolds: 25 Horizon: 2000
nbCores: 16 nbFolds: 25 Horizon: 2000
nbCores: 16 nbFolds: 25 Horizon: 2000


In [5]:
n_cores = 16
n_folds = 25
horizon = 2000

outcome_distribution =  {'spam':0.95,'ham':0.05}

game = games.label_efficient(outcome_distribution)

algos = [ random_algo.Random(  game, horizon, ), 
           feedexp3.FeedExp3(  game, horizon, ),
           feedexp3_v3.FeedExp3(  game, horizon, ),
           cpb.CPB(  game, horizon,)  ] #bpm.BPM(  game, horizon,  [0.5, 0.5 ], np.identity(2) )

colors = [ [0,0,0], [255,128,0], [0,153,0], [204,0,102] ] #'cyan'
labels = ['random', 'FeedExp3 (2001)', 'FeedExp3 (2006)', 'CPB'] #'BPN


fig = go.Figure( )

for alg, color, label in zip( algos, colors, labels):

    r,g,b = color
    result = evaluate_parallel(n_cores, n_folds, horizon, alg, game)
    regret = np.array([ game.delta(i) for i in range(game.n_actions) ]).T @ np.mean(result,0) 
    xcoords = np.arange(0,horizon,1).tolist()
    std = np.array([ game.delta(i) for i in range(game.n_actions) ]).T @ np.std(result,0) 
    upper_regret = regret + std

    fig.add_trace(go.Scatter(x=xcoords, y=regret, line=dict(color='rgb({},{},{})'.format(r,g,b)), mode='lines',  name=label )) # 

    fig.add_trace(   go.Scatter( x=xcoords+xcoords[::-1], y=upper_regret.tolist()+regret.tolist()[::-1],  fill='toself', fillcolor='rgba({},{},{},0.2)'.format(r,g,b), 
                         line=dict(color='rgba(255,255,255,0)'),   hoverinfo="skip",  showlegend=False )

    )
    
fig.show(legend=True)


nbCores: 16 nbFolds: 25 Horizon: 2000
nbCores: 16 nbFolds: 25 Horizon: 2000
nbCores: 16 nbFolds: 25 Horizon: 2000
nbCores: 16 nbFolds: 25 Horizon: 2000


In [4]:
import geometry_v5
import games
import numpy as np
import geometry
outcome_distribution =  {'spam':0.05,'ham':0.95}
game = games.label_efficient(outcome_distribution)
FeedbackMatrix = np.array(  [ [1, 1/2], [1/4, 1/4], [1/4, 1/4] ] )
LossMatrix =  np.array( [ [1, 1],[1, 0],[0, 1] ] )

print('global observability:', geometry.GlobalObservableGame(game) )
print()
print('local observability', geometry.LocalObservableGame(game) )
print()

p = np.array([0.05,0.95])

for i in range(3):
    print('action',i,'expected loss', LossMatrix[i,...].T @ p, 'pareto?', geometry_v5.isParetoOptimal(i, LossMatrix),  )
print()
for pair in  [ [1,2], [2,1]  ]:
    a,b = pair
    print('pair', pair, 'neighbors?', geometry_v5.areNeighbours(a, b, LossMatrix), ' -> neighbohood', geometry_v5.neighborhood(a,b, LossMatrix), 'observable?',
     geometry.ObservablePair(a, b, LossMatrix, [geometry.signal_vecs(i, game.FeedbackMatrix) for i in geometry.Neighbourhood(a, b, LossMatrix)]),
     'delta', (LossMatrix[a,...] - LossMatrix[b,...]).T @ p )

global observability: (True, 'all pairs are globally observable.')

local observability (False, '[2,1] pair is not locally observable.')

action 0 expected loss 1.0000000000000002 pareto? False
action 1 expected loss 0.05 pareto? True
action 2 expected loss 0.9500000000000001 pareto? True

pair [1, 2] neighbors? True  -> neighbohood [1, 2] observable? False delta -0.9
pair [2, 1] neighbors? True  -> neighbohood [1, 2] observable? False delta 0.9000000000000001


In [1]:
import geometry_v5
import games
import numpy as np
import geometry
import geometry_v3
outcome_distribution =  {'spam':0.05,'ham':0.95}
game = games.apple_tasting(False,outcome_distribution)
LossMatrix = np.array( [ [1, 0], [0, 1] ] )
FeedbackMatrix =  np.array([ [1, 1],[1, 0] ])

print('global observability:', geometry.GlobalObservableGame(game) )
print()
print('local observability', geometry.LocalObservableGame(game) )
print()

p = np.array([0.05,0.95])

for i in range(2):
    print('action',i,'expected loss', LossMatrix[i,...].T @ p, 'pareto?', geometry_v5.isParetoOptimal(i, LossMatrix),  )
print()
for pair in  [ [0,1], [1,0]  ]:
    a,b = pair
    print('pair', pair, 'neighbors?', geometry_v5.areNeighbours(a, b, LossMatrix), ' -> neighbohood', geometry_v5.neighborhood(a,b, LossMatrix), 'observable?',
     geometry.ObservablePair(a, b, LossMatrix, [geometry.signal_vecs(i, game.FeedbackMatrix) for i in geometry.Neighbourhood(a, b, LossMatrix)]),
     'delta', (LossMatrix[a,...] - LossMatrix[b,...]).T @ p )

geometry_v3.getV(LossMatrix, game.N, game.M, FeedbackMatrix, game.SignalMatrices, game.mathcal_N, game.V)

global observability: (True, 'all pairs are globally observable.')

local observability (True, 'all neighbouring pairs are observable.')

action 0 expected loss 0.05 pareto? True
action 1 expected loss 0.95 pareto? True

pair [0, 1] neighbors? True  -> neighbohood [0, 1] observable? True delta -0.8999999999999999
pair [1, 0] neighbors? True  -> neighbohood [0, 1] observable? True delta 0.9
Restricted license - for non-production use only - expires 2023-10-25


defaultdict(dict,
            {0: {1: [array([-1.1102198e-16]), array([-1.,  1.])]},
             1: {0: [array([2.22044383e-22]), array([ 1., -1.])]}})